In [1]:
# Bulit the multigraph for the dataset CHI or BER

import pandas as pd
import numpy as np
import torch
import ast
import math
import pickle
def distance(origin, destination):  # Calculate the distance between longitude and latitude points
    lat1, lon1 = origin
    lat2, lon2 = destination
    radius = 6371  # km
    dlat = math.radians(lat2 - lat1)
    dlon = math.radians(lon2 - lon1)
    a = math.sin(dlat / 2) * math.sin(dlat / 2) + math.cos(math.radians(lat1)) \
        * math.cos(math.radians(lat2)) * math.sin(dlon / 2) * math.sin(dlon / 2)
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    d = radius * c
    return d  # return in km


city ='CHI'  # 'BER or CHI'

if city=='BER':
    poi_data=pd.read_csv('yongliu_gowalla_data/Berlin/berlin_poi_incheckin_and_friend.csv')
    checkin_data= pd.read_csv('yongliu_gowalla_data/Berlin/check_in_berlin_user_in_friend.csv')
    friend_ship = pd.read_csv('yongliu_gowalla_data/Berlin/friend_ship_berlin.csv')

elif city=='CHI':
    poi_data=pd.read_csv('yongliu_gowalla_data/Chicago/chi_poi_incheckin_and_friend.csv')
    checkin_data= pd.read_csv('yongliu_gowalla_data/Chicago/check_in_chi_user_in_friend.csv')
    friend_ship = pd.read_csv('yongliu_gowalla_data/Chicago/friend_ship_chi.csv')

poi_data = poi_data.rename(columns={'id': 'Venue_id','lng':'longitude','lat':'latitude'})
checkin_data = checkin_data.rename(columns={'placeid': 'Venue_id'})

print(len(poi_data))
poi_data

5807


Venue_id            created_at  longitude   latitude  photos_count  \
0         9207  2009-02-18T04:45:03Z -87.655835  41.889196             2   
1         9816  2009-03-21T17:27:38Z -87.624448  41.897110            30   
2         9831  2009-03-21T19:12:45Z -87.624571  41.891770            24   
3         9871  2009-03-21T23:38:26Z -87.629984  41.883637             7   
4         9883  2009-03-22T00:23:00Z -87.635869  41.878860            77   
...        ...                   ...        ...        ...           ...   
5802   7413618  2011-05-22T22:13:18Z -87.677789  41.946252             3   
5803   7413632  2011-05-22T22:20:52Z -87.677952  41.946260             2   
5804   7416428  2011-05-23T18:30:05Z -87.634251  41.884626             1   
5805   7430580  2011-05-27T16:02:21Z -87.617665  41.859434             0   
5806   7510632  2011-06-15T20:24:52Z -87.626830  41.896779             2   

      checkins_count  users_count  radius_meters  highlights_count  \
0                172          121             50                 0   
1                595          490             50                 8   
2                252          213            100                 0   
3                129          105             50                 0   
4               1122          810            100                20   
...              ...          ...            ...               ...   
5802              32            3             75                 1   
5803              20            3             35                 0   
5804              11            3             75                 0   
5805              11           11            250                 0   
5806              20           18             75                 3   

      items_count  max_items_count  \
0              13               10   
1              10               10   
2               8               10   
3              10               10   
4              10               10   
...           ...              ...   
5802            0               10   
5803            0               10   
5804            1               10   
5805            1               10   
5806            0               10   

                                        spot_categories  distance_to_center  
0     [{'url': '/categories/121', 'name': 'Corporate...            2.959474  
1     [{'url': '/categories/60', 'name': 'Other - Ar...            1.964245  
2     [{'url': '/categories/445', 'name': 'LEGO Stor...            1.374428  
3      [{'url': '/categories/51', 'name': 'Sculpture'}]            0.768765  
4     [{'url': '/categories/23', 'name': 'Skyscraper'}]            1.105731  
...                                                 ...                 ...  
5802  [{'url': '/categories/223', 'name': 'Basketbal...            8.717138  
5803      [{'url': '/categories/90', 'name': 'Modern'}]            8.724998  
5804  [{'url': '/categories/98', 'name': 'Mediterran...            1.124443  
5805  [{'url': '/categories/213', 'name': 'Planetari...            2.267756  
5806       [{'url': '/categories/67', 'name': 'Wings'}]            1.953537  

[5807 rows x 13 columns]

In [2]:
# Parse the string into an actual list object
friend_ship['user_pair'] = friend_ship['user_pair'].apply(ast.literal_eval)


In [3]:
'''There are 4 types of nodes: user, POI, time, and class'''
# All nodes are sequentially encoded with a unified index in the order: user -> POI -> POI class -> time point

# Create indexes
'''Create indexes using dictionaries''' '''Then convert them into matrix form'''
# Users (user) and POIs (poi) both need indexing

user_check_in = list(set(checkin_data['userid']))
user_check_in_sort = sorted(user_check_in)  # User list
user_dic = {}  # {user_id: user_index}, user index ranging from 0 to 3810
for i in range(len(user_check_in_sort)):
    user_dic[user_check_in_sort[i]] = i

venue_check_in = set(list(checkin_data['Venue_id']))
venue_check_in_sort = list(sorted(list(venue_check_in)))  # POI list
Venue_id_dic = {}  # {POI_id: poi_index}, POI index starting from 0
for i in range(len(venue_check_in_sort)):
    Venue_id_dic[venue_check_in_sort[i]] = i  # The length of user_check_in_sort represents the number of users

# Store the total number of users and POIs
user_number = len(user_check_in_sort)
poi_number = len(venue_check_in_sort)

print("There are", len(user_check_in_sort), "user nodes in this multigraph.")
print("There are", len(venue_check_in_sort), "POI nodes in this multigraph.")

# Create a list of friend relationships {user1_index: user2_index}, friendships are symmetric
friend_list_index = []
friend_list = list(friend_ship['user_pair'])

# Convert user IDs to their corresponding index values
for i in range(len(friend_list)):
    friend_list_index.append((user_dic[friend_list[i][0]], user_dic[friend_list[i][1]]))

print(friend_list_index[:10])

# Create a dictionary of friendship edges
friend_edge = {}
for i in range(len(friend_list_index)):
    friend_edge[i] = {friend_list_index[i][0], friend_list_index[i][1]}

# Save the friend list edges using npy format (for hmgcl)
np.save("multigraph/" + city + "/friend_list_index.npy", torch.tensor(np.array(friend_list_index)).t().contiguous())  # Save the friend list edges


There are 6444 user nodes in this multigraph.
There are 5807 POI nodes in this multigraph.
[(0, 2787), (0, 1), (0, 2), (0, 3), (0, 5202), (0, 596), (0, 4), (0, 165), (0, 5), (0, 6)]


In [4]:
# Modify poi_data

# Parse the string into an actual list object
poi_data['spot_categories'] = poi_data['spot_categories'].apply(ast.literal_eval)

# Extract 'url' and 'name' and create new columns
poi_data['url'] = poi_data['spot_categories'].apply(lambda x: x[0]['url'] if x else None)
poi_data['category'] = poi_data['spot_categories'].apply(lambda x: x[0]['name'] if x else None)

poi_data


Venue_id            created_at  longitude   latitude  photos_count  \
0         9207  2009-02-18T04:45:03Z -87.655835  41.889196             2   
1         9816  2009-03-21T17:27:38Z -87.624448  41.897110            30   
2         9831  2009-03-21T19:12:45Z -87.624571  41.891770            24   
3         9871  2009-03-21T23:38:26Z -87.629984  41.883637             7   
4         9883  2009-03-22T00:23:00Z -87.635869  41.878860            77   
...        ...                   ...        ...        ...           ...   
5802   7413618  2011-05-22T22:13:18Z -87.677789  41.946252             3   
5803   7413632  2011-05-22T22:20:52Z -87.677952  41.946260             2   
5804   7416428  2011-05-23T18:30:05Z -87.634251  41.884626             1   
5805   7430580  2011-05-27T16:02:21Z -87.617665  41.859434             0   
5806   7510632  2011-06-15T20:24:52Z -87.626830  41.896779             2   

      checkins_count  users_count  radius_meters  highlights_count  \
0                172          121             50                 0   
1                595          490             50                 8   
2                252          213            100                 0   
3                129          105             50                 0   
4               1122          810            100                20   
...              ...          ...            ...               ...   
5802              32            3             75                 1   
5803              20            3             35                 0   
5804              11            3             75                 0   
5805              11           11            250                 0   
5806              20           18             75                 3   

      items_count  max_items_count  \
0              13               10   
1              10               10   
2               8               10   
3              10               10   
4              10               10   
...           ...              ...   
5802            0               10   
5803            0               10   
5804            1               10   
5805            1               10   
5806            0               10   

                                        spot_categories  distance_to_center  \
0     [{'url': '/categories/121', 'name': 'Corporate...            2.959474   
1     [{'url': '/categories/60', 'name': 'Other - Ar...            1.964245   
2     [{'url': '/categories/445', 'name': 'LEGO Stor...            1.374428   
3      [{'url': '/categories/51', 'name': 'Sculpture'}]            0.768765   
4     [{'url': '/categories/23', 'name': 'Skyscraper'}]            1.105731   
...                                                 ...                 ...   
5802  [{'url': '/categories/223', 'name': 'Basketbal...            8.717138   
5803      [{'url': '/categories/90', 'name': 'Modern'}]            8.724998   
5804  [{'url': '/categories/98', 'name': 'Mediterran...            1.124443   
5805  [{'url': '/categories/213', 'name': 'Planetari...            2.267756   
5806       [{'url': '/categories/67', 'name': 'Wings'}]            1.953537   

                  url              category  
0     /categories/121      Corporate Office  
1      /categories/60  Other - Architecture  
2     /categories/445            LEGO Store  
3      /categories/51             Sculpture  
4      /categories/23            Skyscraper  
...               ...                   ...  
5802  /categories/223      Basketball Court  
5803   /categories/90                Modern  
5804   /categories/98         Mediterranean  
5805  /categories/213           Planetarium  
5806   /categories/67                 Wings  

[5807 rows x 15 columns]

In [5]:
poi_data['Venue_id_index']= poi_data['Venue_id'].map(Venue_id_dic)
poi_data

Venue_id            created_at  longitude   latitude  photos_count  \
0         9207  2009-02-18T04:45:03Z -87.655835  41.889196             2   
1         9816  2009-03-21T17:27:38Z -87.624448  41.897110            30   
2         9831  2009-03-21T19:12:45Z -87.624571  41.891770            24   
3         9871  2009-03-21T23:38:26Z -87.629984  41.883637             7   
4         9883  2009-03-22T00:23:00Z -87.635869  41.878860            77   
...        ...                   ...        ...        ...           ...   
5802   7413618  2011-05-22T22:13:18Z -87.677789  41.946252             3   
5803   7413632  2011-05-22T22:20:52Z -87.677952  41.946260             2   
5804   7416428  2011-05-23T18:30:05Z -87.634251  41.884626             1   
5805   7430580  2011-05-27T16:02:21Z -87.617665  41.859434             0   
5806   7510632  2011-06-15T20:24:52Z -87.626830  41.896779             2   

      checkins_count  users_count  radius_meters  highlights_count  \
0                172          121             50                 0   
1                595          490             50                 8   
2                252          213            100                 0   
3                129          105             50                 0   
4               1122          810            100                20   
...              ...          ...            ...               ...   
5802              32            3             75                 1   
5803              20            3             35                 0   
5804              11            3             75                 0   
5805              11           11            250                 0   
5806              20           18             75                 3   

      items_count  max_items_count  \
0              13               10   
1              10               10   
2               8               10   
3              10               10   
4              10               10   
...           ...              ...   
5802            0               10   
5803            0               10   
5804            1               10   
5805            1               10   
5806            0               10   

                                        spot_categories  distance_to_center  \
0     [{'url': '/categories/121', 'name': 'Corporate...            2.959474   
1     [{'url': '/categories/60', 'name': 'Other - Ar...            1.964245   
2     [{'url': '/categories/445', 'name': 'LEGO Stor...            1.374428   
3      [{'url': '/categories/51', 'name': 'Sculpture'}]            0.768765   
4     [{'url': '/categories/23', 'name': 'Skyscraper'}]            1.105731   
...                                                 ...                 ...   
5802  [{'url': '/categories/223', 'name': 'Basketbal...            8.717138   
5803      [{'url': '/categories/90', 'name': 'Modern'}]            8.724998   
5804  [{'url': '/categories/98', 'name': 'Mediterran...            1.124443   
5805  [{'url': '/categories/213', 'name': 'Planetari...            2.267756   
5806       [{'url': '/categories/67', 'name': 'Wings'}]            1.953537   

                  url              category  Venue_id_index  
0     /categories/121      Corporate Office               0  
1      /categories/60  Other - Architecture               1  
2     /categories/445            LEGO Store               2  
3      /categories/51             Sculpture               3  
4      /categories/23            Skyscraper               4  
...               ...                   ...             ...  
5802  /categories/223      Basketball Court            5802  
5803   /categories/90                Modern            5803  
5804   /categories/98         Mediterranean            5804  
5805  /categories/213           Planetarium            5805  
5806   /categories/67                 Wings            5806  

[5807 rows x 16 columns]

In [6]:
# poi_lat_lon = dict(enumerate(zip(poi_data['latitude'], poi_data['longitude'])))
# Create dictionary with Venue_id as keys and (latitude, longitude) as values
poi_lat_lon  = {row['Venue_id']: (row['latitude'], row['longitude']) for _, row in poi_data.iterrows()}
poi_lat_lon

{9207: (41.8891957606, -87.6558351517),
 9816: (41.8971103352, -87.6244479418),
 9831: (41.89177035, -87.6245713167),
 9871: (41.8836366032, -87.6299840212),
 9883: (41.8788598144, -87.6358687878),
 9889: (41.8778443333, -87.63545035),
 9905: (41.8927145, -87.61360645),
 9907: (41.8917036129, -87.6074802876),
 9935: (41.9385440066, -87.6444545388),
 9938: (41.94006085, -87.6498055333),
 9939: (41.9410586333, -87.65152215),
 9943: (41.8654847, -87.61699675),
 9948: (41.8623379996, -87.6166909933),
 9952: (41.879578752, -87.6228868961),
 9958: (41.9424319167, -87.6446342333),
 9996: (41.8676090167, -87.6146364167),
 10576: (41.8762671833, -87.62439965),
 10600: (41.8578779667, -87.6239705),
 10601: (41.8578565, -87.6219964),
 10602: (41.8570840333, -87.6221895167),
 10605: (41.8575882833, -87.6207733),
 10608: (41.8679738, -87.6197648),
 10610: (41.8661284333, -87.61264085),
 10611: (41.8663108333, -87.6104521667),
 10616: (41.8663969455, -87.6067829132),
 10621: (41.8790245, -87.6245713

In [7]:
checkin_data

userid  Venue_id              datetime
0         1338     11601  2010-05-30T16:45:54Z
1         5144    170134  2010-04-25T02:22:57Z
2       113934    610907  2011-05-26T12:03:19Z
3       113934    244626  2011-05-25T22:12:22Z
4       113934    404377  2011-05-25T20:50:35Z
...        ...       ...                   ...
185814  272605     53925  2010-08-14T21:45:24Z
185815  272605    458722  2010-08-13T05:14:05Z
185816  272605    450825  2010-05-17T18:40:46Z
185817  281929    354326  2011-01-27T16:47:34Z
185818   56681    173892  2010-07-02T20:32:18Z

[185819 rows x 3 columns]

In [8]:
# Modify check-in data

def time_fenge(hour):  # The range of values is [0, 23], dividing the day into 4 time segments
    # Divide the day into four segments:
    # 22:00 - 05:00, 05:00 - 10:00, 10:00 - 15:00, 15:00 - 22:00 (for embedding purposes)
    if 5 <= hour < 10:
        return 1
    elif 10 <= hour < 15:
        return 2
    elif 15 <= hour < 22:
        return 3
    elif 22 <= hour or hour < 5:
        return 0


In [9]:
# Convert time data to pandas datetime format
checkin_data['timestamp'] = pd.to_datetime(checkin_data['datetime'], format='%Y-%m-%dT%H:%M:%SZ')

# Extract year, month, day, and hour
checkin_data['year'] = checkin_data['timestamp'].dt.year
checkin_data['month'] = checkin_data['timestamp'].dt.month
checkin_data['day'] = checkin_data['timestamp'].dt.day
checkin_data['hour'] = checkin_data['timestamp'].dt.hour

# Get the weekday as a number (0 represents Monday, 6 represents Sunday)
checkin_data['weekday_num'] = checkin_data['timestamp'].dt.weekday

# Convert to Unix timestamp (in seconds)
checkin_data['unix_time'] = checkin_data['timestamp'].view('int64') // 10**9

# Create a 'date_yday' column by concatenating year, month, and day
checkin_data['date_yday'] = checkin_data['year'].astype(str) + '_' + checkin_data['month'].astype(str) + '_' + checkin_data['day'].astype(str)

# Count the number of unique dates
unique_days_count = checkin_data['timestamp'].dt.date.nunique()

# Print the result to check the output
print(f"There are {unique_days_count} unique days.")

checkin_data


C:\Users\28593\AppData\Local\Temp\ipykernel_92168\3588684638.py:14: FutureWarning: Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.
  checkin_data['unix_time'] = checkin_data['timestamp'].view('int64') // 10**9


There are 770 unique days.


userid  Venue_id              datetime           timestamp  year  \
0         1338     11601  2010-05-30T16:45:54Z 2010-05-30 16:45:54  2010   
1         5144    170134  2010-04-25T02:22:57Z 2010-04-25 02:22:57  2010   
2       113934    610907  2011-05-26T12:03:19Z 2011-05-26 12:03:19  2011   
3       113934    244626  2011-05-25T22:12:22Z 2011-05-25 22:12:22  2011   
4       113934    404377  2011-05-25T20:50:35Z 2011-05-25 20:50:35  2011   
...        ...       ...                   ...                 ...   ...   
185814  272605     53925  2010-08-14T21:45:24Z 2010-08-14 21:45:24  2010   
185815  272605    458722  2010-08-13T05:14:05Z 2010-08-13 05:14:05  2010   
185816  272605    450825  2010-05-17T18:40:46Z 2010-05-17 18:40:46  2010   
185817  281929    354326  2011-01-27T16:47:34Z 2011-01-27 16:47:34  2011   
185818   56681    173892  2010-07-02T20:32:18Z 2010-07-02 20:32:18  2010   

        month  day  hour  weekday_num   unix_time  date_yday  
0           5   30    16            6  1275237954  2010_5_30  
1           4   25     2            6  1272162177  2010_4_25  
2           5   26    12            3  1306411399  2011_5_26  
3           5   25    22            2  1306361542  2011_5_25  
4           5   25    20            2  1306356635  2011_5_25  
...       ...  ...   ...          ...         ...        ...  
185814      8   14    21            5  1281822324  2010_8_14  
185815      8   13     5            4  1281676445  2010_8_13  
185816      5   17    18            0  1274121646  2010_5_17  
185817      1   27    16            3  1296146854  2011_1_27  
185818      7    2    20            4  1278102738   2010_7_2  

[185819 rows x 11 columns]

In [10]:
# Read the 'hour' column and process it using the time_fenge function
checkin_data['hour_periods'] = checkin_data['hour'].apply(time_fenge)

# Map 'Venue_id' to latitude and longitude
checkin_data['lat_lon'] = checkin_data['Venue_id'].map(poi_lat_lon)

# Map 'userid' and 'Venue_id' to their respective indices
checkin_data['userid_index'] = checkin_data['userid'].map(user_dic)
checkin_data['Venue_id_index'] = checkin_data['Venue_id'].map(Venue_id_dic)

checkin_data


userid  Venue_id              datetime           timestamp  year  \
0         1338     11601  2010-05-30T16:45:54Z 2010-05-30 16:45:54  2010   
1         5144    170134  2010-04-25T02:22:57Z 2010-04-25 02:22:57  2010   
2       113934    610907  2011-05-26T12:03:19Z 2011-05-26 12:03:19  2011   
3       113934    244626  2011-05-25T22:12:22Z 2011-05-25 22:12:22  2011   
4       113934    404377  2011-05-25T20:50:35Z 2011-05-25 20:50:35  2011   
...        ...       ...                   ...                 ...   ...   
185814  272605     53925  2010-08-14T21:45:24Z 2010-08-14 21:45:24  2010   
185815  272605    458722  2010-08-13T05:14:05Z 2010-08-13 05:14:05  2010   
185816  272605    450825  2010-05-17T18:40:46Z 2010-05-17 18:40:46  2010   
185817  281929    354326  2011-01-27T16:47:34Z 2011-01-27 16:47:34  2011   
185818   56681    173892  2010-07-02T20:32:18Z 2010-07-02 20:32:18  2010   

        month  day  hour  weekday_num   unix_time  date_yday  hour_periods  \
0           5   30    16            6  1275237954  2010_5_30             3   
1           4   25     2            6  1272162177  2010_4_25             0   
2           5   26    12            3  1306411399  2011_5_26             2   
3           5   25    22            2  1306361542  2011_5_25             0   
4           5   25    20            2  1306356635  2011_5_25             3   
...       ...  ...   ...          ...         ...        ...           ...   
185814      8   14    21            5  1281822324  2010_8_14             3   
185815      8   13     5            4  1281676445  2010_8_13             1   
185816      5   17    18            0  1274121646  2010_5_17             3   
185817      1   27    16            3  1296146854  2011_1_27             3   
185818      7    2    20            4  1278102738   2010_7_2             3   

                                lat_lon  userid_index  Venue_id_index  
0       (41.8301289642, -87.6342594624)            93              33  
1       (41.8916677203, -87.6245729729)           286            1229  
2           (41.79035371, -87.74016481)          2511            3419  
3             (41.7742525, -87.7422931)          2511            1683  
4       (41.7729635605, -87.7424319837)          2511            2403  
...                                 ...           ...             ...  
185814   (41.884346501, -87.6328834891)          4286             493  
185815     (41.8856159, -87.8026364833)          4286            2658  
185816  (41.8819994885, -87.6278244019)          4286            2627  
185817  (41.8732289193, -87.6241459505)          4360            2167  
185818  (41.9226801333, -87.6970767833)          1398            1256  

[185819 rows x 15 columns]

In [11]:
# Record the number of user check-ins for each hour and convert it into a percentage

# Initialize a dictionary to count check-ins for each hour (0-23)
times = {}
for i in range(24):
    times[str(i)] = 0

# Count check-ins for each hour
for index, row in checkin_data.iterrows():
    times[str(row['hour'])] += 1

# Convert the counts into percentages
times_ratio = {}
for i in range(24):
    times_ratio[str(i)] = (times[str(i)] / checkin_data.shape[0]) * 100
    print(times_ratio[str(i)])


7.935679343877644
6.542388022753324
5.341219143359936
4.0211173238474
2.8151050215532316
1.8571836033990066
1.0999951565770991
0.5747528508925352
0.470888337575813
0.23786588023829638
0.3196659114514662
0.9326279874501532
1.8501875480978802
3.415689461249926
4.375225353704412
4.438189851414549
5.174390132333077
7.141357988149759
7.200017221059203
6.4950301099457
6.051049677374219
6.138231289588255
7.369537022586495
8.20260576152062


In [12]:
poi_data

Venue_id            created_at  longitude   latitude  photos_count  \
0         9207  2009-02-18T04:45:03Z -87.655835  41.889196             2   
1         9816  2009-03-21T17:27:38Z -87.624448  41.897110            30   
2         9831  2009-03-21T19:12:45Z -87.624571  41.891770            24   
3         9871  2009-03-21T23:38:26Z -87.629984  41.883637             7   
4         9883  2009-03-22T00:23:00Z -87.635869  41.878860            77   
...        ...                   ...        ...        ...           ...   
5802   7413618  2011-05-22T22:13:18Z -87.677789  41.946252             3   
5803   7413632  2011-05-22T22:20:52Z -87.677952  41.946260             2   
5804   7416428  2011-05-23T18:30:05Z -87.634251  41.884626             1   
5805   7430580  2011-05-27T16:02:21Z -87.617665  41.859434             0   
5806   7510632  2011-06-15T20:24:52Z -87.626830  41.896779             2   

      checkins_count  users_count  radius_meters  highlights_count  \
0                172          121             50                 0   
1                595          490             50                 8   
2                252          213            100                 0   
3                129          105             50                 0   
4               1122          810            100                20   
...              ...          ...            ...               ...   
5802              32            3             75                 1   
5803              20            3             35                 0   
5804              11            3             75                 0   
5805              11           11            250                 0   
5806              20           18             75                 3   

      items_count  max_items_count  \
0              13               10   
1              10               10   
2               8               10   
3              10               10   
4              10               10   
...           ...              ...   
5802            0               10   
5803            0               10   
5804            1               10   
5805            1               10   
5806            0               10   

                                        spot_categories  distance_to_center  \
0     [{'url': '/categories/121', 'name': 'Corporate...            2.959474   
1     [{'url': '/categories/60', 'name': 'Other - Ar...            1.964245   
2     [{'url': '/categories/445', 'name': 'LEGO Stor...            1.374428   
3      [{'url': '/categories/51', 'name': 'Sculpture'}]            0.768765   
4     [{'url': '/categories/23', 'name': 'Skyscraper'}]            1.105731   
...                                                 ...                 ...   
5802  [{'url': '/categories/223', 'name': 'Basketbal...            8.717138   
5803      [{'url': '/categories/90', 'name': 'Modern'}]            8.724998   
5804  [{'url': '/categories/98', 'name': 'Mediterran...            1.124443   
5805  [{'url': '/categories/213', 'name': 'Planetari...            2.267756   
5806       [{'url': '/categories/67', 'name': 'Wings'}]            1.953537   

                  url              category  Venue_id_index  
0     /categories/121      Corporate Office               0  
1      /categories/60  Other - Architecture               1  
2     /categories/445            LEGO Store               2  
3      /categories/51             Sculpture               3  
4      /categories/23            Skyscraper               4  
...               ...                   ...             ...  
5802  /categories/223      Basketball Court            5802  
5803   /categories/90                Modern            5803  
5804   /categories/98         Mediterranean            5804  
5805  /categories/213           Planetarium            5805  
5806   /categories/67                 Wings            5806  

[5807 rows x 16 columns]

In [14]:
import folium
# Instantiate a feature group for the incidents in the dataframe
latitude =  41.87950259199219
longitude = -87.6225409728181
# BER:  52.5190838018783, 13.401522103237626

del_cat=["Moving Target","Other Great Outdoors","Plane"]
incidents = folium.map.FeatureGroup()
for index,row in poi_data.iterrows():

    lat=row['latitude']
    lon= row['longitude']
#     wgs_lon, wgs_lat = gcj2wgs(lon, lat)
    incidents.add_child(
        folium.CircleMarker(
            [lat, lon],
            radius=5, # define how big you want the circle markers to be
            color='yellow',#yellow
#             fill=False,
            fill=True,
            fill_color='red',
            fill_opacity=0.5
        )
    )
# Add incidents to map
san_map = folium.Map(location=[latitude, longitude],
                     control_scale=True,
                     # tiles='https://stamen-tiles-{s}.a.ssl.fastly.net/terrain/{z}/{x}/{y}{r}.jpg',
                     attr='OpenStreetMap attribution',
                     zoom_start=12)
san_map.add_child(incidents)

In [15]:
# Convert the check-in relationships into edges, forming a directed graph between users and POIs

# The visit edge is an asymmetric edge, with edge features defined as
# the number of visits in four different time periods. If there are no visits, the value is set to 0.
# Number of features: 4

# The revisit edge is also an asymmetric edge, with edge features defined as
# the number of visits in four different time periods. If there are no visits, the value is set to 0.
# Number of features: 4. This edge is symmetric to the visit edge, but the starting and ending node types are different.


from collections import defaultdict

# Initialize a dictionary to store the visit counts and time period statistics
# for each (userid_index, Venue_id_index) pair
visit_edge_dict = defaultdict(lambda: [0, 0, 0, 0])  # Each edge feature is initialized as [0, 0, 0, 0]

# Iterate through checkin_data to count visits and categorize them by time period
for _, row in checkin_data.iterrows():
    user_poi_pair = (row['userid_index'], row['Venue_id_index'])
    hour_period = row['hour_periods']
    visit_edge_dict[user_poi_pair][hour_period] += 1

# Generate visit_list_edge and visit_list_edge_attr
visit_list_edge = sorted(visit_edge_dict.keys())  # Sorted list of (user, POI) pairs
visit_list_edge_attr = [visit_edge_dict[edge] for edge in visit_list_edge]  # Corresponding edge features

# Generate re_visit_list_edge and re_visit_list_edge_attr (by swapping user and POI order)
re_visit_list_edge = [(poi, user) for user, poi in visit_list_edge]
re_visit_list_edge_attr = visit_list_edge_attr  # The features of symmetric edges remain the same


In [16]:
visit_list_edge_attr

[[0, 0, 1, 0],
 [0, 1, 0, 0],
 [1, 0, 0, 0],
 [0, 0, 0, 2],
 [0, 0, 1, 0],
 [0, 0, 0, 1],
 [1, 0, 0, 0],
 [0, 0, 0, 1],
 [2, 0, 1, 1],
 [1, 0, 0, 0],
 [0, 0, 0, 1],
 [0, 0, 0, 1],
 [1, 0, 0, 0],
 [1, 0, 0, 0],
 [0, 0, 0, 1],
 [0, 0, 0, 1],
 [0, 1, 0, 2],
 [0, 0, 0, 1],
 [0, 0, 0, 1],
 [0, 0, 1, 0],
 [0, 1, 0, 0],
 [1, 1, 0, 0],
 [0, 0, 0, 1],
 [0, 0, 1, 0],
 [2, 0, 0, 0],
 [0, 0, 1, 0],
 [1, 0, 0, 0],
 [1, 0, 0, 0],
 [0, 0, 0, 2],
 [0, 0, 0, 1],
 [0, 1, 0, 0],
 [1, 0, 0, 0],
 [1, 0, 0, 0],
 [1, 0, 0, 0],
 [1, 0, 0, 0],
 [1, 0, 0, 0],
 [0, 0, 0, 1],
 [0, 0, 0, 1],
 [1, 0, 0, 0],
 [1, 0, 0, 1],
 [0, 0, 0, 1],
 [0, 0, 1, 0],
 [1, 0, 0, 0],
 [1, 0, 1, 0],
 [0, 0, 1, 0],
 [0, 0, 0, 1],
 [1, 0, 0, 0],
 [0, 0, 1, 0],
 [0, 0, 1, 0],
 [0, 0, 0, 1],
 [0, 0, 0, 2],
 [0, 0, 0, 1],
 [0, 0, 0, 1],
 [1, 0, 0, 0],
 [0, 0, 0, 1],
 [1, 0, 1, 0],
 [0, 0, 0, 1],
 [1, 0, 0, 0],
 [0, 0, 0, 1],
 [1, 0, 0, 0],
 [0, 0, 0, 2],
 [0, 0, 0, 1],
 [1, 0, 0, 0],
 [1, 0, 0, 0],
 [0, 0, 0, 1],
 [2, 0, 2, 1],
 [3, 0, 0,

In [17]:
# Convert visit_list_edge_attr to tensor format compatible with data structures
# visit_list_edge_attr = torch.tensor(np.array(visit_list_edge_attr).reshape(1,-1)).t().contiguous()

# Save visit and revisit edges and their attributes in .npy format

# Save user -> visit -> POI directed edges
np.save("multigraph/" + city + "/visit_list_edge_tensor.npy", torch.tensor(np.array(visit_list_edge)).t().contiguous())

# Save user -> visit -> POI directed edge features (visit counts in different time periods)
np.save("multigraph/" + city + "/visit_list_edge_attr.npy", torch.tensor(np.array(visit_list_edge_attr)))

# Save POI -> revisit -> user directed edges
np.save("multigraph/" + city + "/revisit_list_edge_tensor.npy", torch.tensor(np.array(re_visit_list_edge)).t().contiguous())

# Save POI -> revisit -> user directed edge features (visit counts in different time periods)
np.save("multigraph/" + city + "/revisit_list_edge_attr.npy", torch.tensor(np.array(re_visit_list_edge_attr)))


In [18]:
# No need to explicitly convert to a list, operations can be performed directly on the groupby object
grouped = checkin_data.groupby('userid_index')

# Use a dictionary to store the home coordinates of users
user_home = {}

# Iterate through each group and calculate the average latitude and longitude using aggregation functions
for userid, group in grouped:
    # Extract lat_lon and use pandas' aggregation method to compute the mean values
    lat_aver = group['lat_lon'].apply(lambda x: x[0]).mean()
    lon_aver = group['lat_lon'].apply(lambda x: x[1]).mean()

    # Store the result in the dictionary
    user_home[userid] = (lat_aver, lon_aver)

user_home


{0: (41.7874410169, -87.744884491),
 1: (41.87939, -87.6178),
 2: (41.97476643, -87.8902602196),
 3: (41.88470418151, -87.62975414032665),
 4: (41.8489151418, -87.71047723715),
 5: (41.7874410169, -87.744884491),
 6: (41.88363593571666, -87.6245829798),
 7: (41.88047159426666, -87.62948096168333),
 8: (41.88281650827119, -87.63072339455424),
 9: (41.9329876394, -87.66194434697142),
 10: (41.889378167245155, -87.63264317467097),
 11: (41.9792656114, -87.86436211951936),
 12: (41.7874410169, -87.744884491),
 13: (41.907378296919994, -87.65090702086),
 14: (41.91522073398334, -87.63925276563333),
 15: (41.88662505782198, -87.63586351089613),
 16: (41.85499352473077, -87.66321828874615),
 17: (41.883985813816, -87.64209144589599),
 18: (41.87939, -87.6178),
 19: (41.89308302006666, -87.6244911827),
 20: (41.890042707744854, -87.62622758944666),
 21: (41.8953613865, -87.6252043247),
 22: (41.834825252505574, -87.68943405167217),
 23: (41.7874410169, -87.744884491),
 24: (41.89077339940833, 

In [19]:
from collections import defaultdict

# Meeting relationship for friend edges
# Friend edges are symmetric, and the edge features are defined as:
# - The number of meetings in four different time periods
# - The distance between the users' homes
# Number of features: 5

group = checkin_data.groupby("Venue_id")  # Group data by Venue_id
group = list(group)

meeting_Threshold = 1800 * 2  # Time threshold for a meeting (in seconds)
# 1800s is 0.5 hours, so this threshold represents meetings within 1 hour

# Initialize a dictionary to store meeting counts and home distance for each (user1, user2) pair
# Using a tuple (user1, user2) as the key avoids string concatenation
friend_list_dict_attr = defaultdict(lambda: [0, 0, 0, 0, 0])  # Default feature values [0, 0, 0, 0, 0]

# Compute meeting occurrences
for i, (venue_id, df) in enumerate(group):
    print(f"Processing group {i} for venue {venue_id}")

    # Sort data by timestamp to reduce unnecessary comparisons
    df = df.sort_values('unix_time').reset_index(drop=True)

    # Use NumPy vectorized computation to calculate time differences, avoiding nested loops
    time_diffs = np.abs(df['unix_time'].values[:, None] - df['unix_time'].values)

    # Use a boolean mask to filter user pairs with time differences below the threshold
    meeting_mask = (time_diffs < meeting_Threshold) & (time_diffs > 0)

    # Iterate through user pairs that meet the meeting conditions
    for idx1, idx2 in zip(*np.where(meeting_mask)):
        user1, user2 = df.iloc[idx1]['userid_index'], df.iloc[idx2]['userid_index']
        hour_per = df.iloc[idx1]['hour_periods']

        # Check if the users are friends
        if (user1, user2) in friend_list_index:
            friend_list_dict_attr[(user1, user2)][hour_per] += 1
        elif (user2, user1) in friend_list_index:
            friend_list_dict_attr[(user2, user1)][hour_per] += 1

# Compute the home distance between friends and add it to the feature set
friend_edge_attr = []
for user1, user2 in friend_list_index:
    # Compute the distance between users' homes
    dis = distance(user_home[user1], user_home[user2])

    # Update the distance information in the feature list
    friend_list_dict_attr[(user1, user2)][4] = dis

    # Append the feature list to friend_edge_attr
    friend_edge_attr.append(friend_list_dict_attr[(user1, user2)])

# Convert to a NumPy array
friend_edge_attr = np.array(friend_edge_attr)
print(friend_edge_attr)


Processing group 0 for venue 9207
Processing group 1 for venue 9816
Processing group 2 for venue 9831
Processing group 3 for venue 9871
Processing group 4 for venue 9883
Processing group 5 for venue 9889
Processing group 6 for venue 9905
Processing group 7 for venue 9907
Processing group 8 for venue 9935
Processing group 9 for venue 9938
Processing group 10 for venue 9939
Processing group 11 for venue 9943
Processing group 12 for venue 9948
Processing group 13 for venue 9952
Processing group 14 for venue 9958
Processing group 15 for venue 9996
Processing group 16 for venue 10576
Processing group 17 for venue 10600
Processing group 18 for venue 10601
Processing group 19 for venue 10602
Processing group 20 for venue 10605
Processing group 21 for venue 10608
Processing group 22 for venue 10610
Processing group 23 for venue 10611
Processing group 24 for venue 10616
Processing group 25 for venue 10621
Processing group 26 for venue 10670
Processing group 27 for venue 10987
Processing group 2

In [20]:
np.save("multigraph/" + city + "/friend_edge_attr.npy", friend_edge_attr)  # Number of features: 5


In [21]:
import numpy as np
import torch
import math

# The distance function remains unchanged and is used to calculate the distance between latitude and longitude coordinates.
'''If you need to compute distances in bulk (e.g., processing distances for a large number of users and POIs),
the first function (based on numpy) is more suitable as it handles large-scale vectorized computations more efficiently.'''

def distance(lat1, lon1, lat2, lon2):  # This version is suitable for large-scale computations
    radius = 6371  # Earth's radius in kilometers
    dlat = np.radians(lat2 - lat1)
    dlon = np.radians(lon2 - lon1)
    a = np.sin(dlat / 2) ** 2 + np.cos(np.radians(lat1)) * np.cos(np.radians(lat2)) * np.sin(dlon / 2) ** 2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))
    d = radius * c
    return d

def POi_live_with_user(poi_data, user_home):
    live_with = []
    live_with_attr = []
    re_live_with = []
    re_live_with_attr = []

    # Extract POI coordinates (latitude, longitude, and Venue_id_index)
    poi_coords = poi_data[['latitude', 'longitude', 'Venue_id_index']].to_numpy()

    # Iterate over each user
    for user_id, (lat_user, lon_user) in user_home.items():
        # Compute distances in bulk between the user and all POIs
        distances = distance(lat_user, lon_user, poi_coords[:, 0], poi_coords[:, 1])

        # Select POIs within a distance of 1.5 km
        close_poi_indices = np.where(distances <= 1.5)[0]

        # Record edges and distance attributes for each qualifying POI
        for poi_idx in close_poi_indices:
            venue_id = int(poi_coords[poi_idx, 2])
            dis = distances[poi_idx]
            live_with.append((venue_id, user_id))  # POI -> user edge
            re_live_with.append((user_id, venue_id))  # user -> POI edge
            live_with_attr.append(dis)  # Edge attribute: distance
            re_live_with_attr.append(dis)

    # Convert results to tensor and numpy arrays
    live_with = torch.tensor(live_with, dtype=torch.long).t().contiguous()
    re_live_with = torch.tensor(re_live_with, dtype=torch.long).t().contiguous()
    live_with_attr = np.array(live_with_attr).reshape(-1, 1)
    re_live_with_attr = np.array(re_live_with_attr).reshape(-1, 1)
    return live_with, live_with_attr, re_live_with, re_live_with_attr

# Call the function
live_with_edge, live_with_attr, re_live_with_edge, re_live_with_attr = POi_live_with_user(poi_data, user_home)


In [22]:
np.save("multigraph/"+city+"/live_with_edge.npy",live_with_edge)
np.save("multigraph/"+city+"/live_with_attr.npy",live_with_attr)
np.save("multigraph/"+city+"/re_live_with_edge.npy",re_live_with_edge)
np.save("multigraph/"+city+"/re_live_with_attr.npy",re_live_with_attr)
live_with_attr

array([[0.        ],
       [0.70127605],
       [0.54595041],
       ...,
       [1.43160597],
       [1.39631989],
       [0.75935222]])

In [23]:
'''Relationship between POIs: co-occurrence relationship and same-category relationship'''

# First, process the same-category relationship
def POi_class_same_POI(poi_data):
    # POIs of the same category are connected by an edge
    # The edges are stored as bidirectional edges

    class_same_edge = []
    class_same_edge_attr = []

    # Group POIs by category
    grouped = poi_data.groupby('category')

    for category, group in grouped:
        poi_indices = group.index.to_numpy()  # POI indices
        latitudes = group['latitude'].to_numpy()
        longitudes = group['longitude'].to_numpy()

        # Compute distances between every pair of POIs, avoiding duplicates and self-loops
        for i in range(len(poi_indices)):
            for j in range(i + 1, len(poi_indices)):
                index1, index2 = poi_indices[i], poi_indices[j]

                # Calculate the distance between POIs
                dis = distance(latitudes[i], longitudes[i], latitudes[j], longitudes[j])

                # Add bidirectional edges
                class_same_edge.append((index1, index2))
                class_same_edge.append((index2, index1))

                # Store edge attributes (same category, distance)
                class_same_edge_attr.append((1, dis))
                class_same_edge_attr.append((1, dis))

    # Convert to tensor and numpy array
    class_same_edge = torch.tensor(np.array(class_same_edge), dtype=torch.long).t().contiguous()

    return class_same_edge, class_same_edge_attr

# Call the function
class_same_edge, class_same_edge_attr = POi_class_same_POI(poi_data)


In [24]:
np.save("multigraph/"+city+"/class_same_edge.npy",class_same_edge)
np.save("multigraph/"+city+"/class_same_edge_attr.npy",class_same_edge_attr)

In [25]:
# Initialize co-occurrence edges (fully connected graph)
co_occurrence_list_index = [(i, j) for i in range(poi_data.shape[0]) for j in range(poi_data.shape[0]) if i != j]

# Initialize a dictionary for co-occurrence edge attributes
# The attributes include co-occurrence count and distance
co_occurrence_list_dict_attr = {f"{u_poi}+{v_poi}": [0, 0] for (u_poi, v_poi) in co_occurrence_list_index}


In [26]:
## Count the co-occurrence frequency between pairs of POIs

# Sort checkin_data by 'userid_index' and group by user
checkin_data = checkin_data.sort_values('userid_index', ascending=True)
group2 = checkin_data.groupby("userid_index")

# Iterate through each user's visit trajectory
for user_index, user_data in group2:
    if user_index % 300 == 0:
        print(user_index)

    # Extract the user's visit trajectory and remove duplicates
    venue_ids = user_data['Venue_id_index'].to_numpy()
    unique_venues, counts = np.unique(venue_ids, return_counts=True)  # Extract unique POIs and their visit counts

    # Iterate through unique POI pairs
    for i in range(len(unique_venues)):
        for j in range(i + 1, len(unique_venues)):
            # Compute the co-occurrence count between two POIs
            poi_poi_count = counts[i] * counts[j]
            poi1, poi2 = unique_venues[i], unique_venues[j]

            # Update the dictionary with co-occurrence counts (bidirectional update)
            co_occurrence_list_dict_attr[f"{poi1}+{poi2}"][0] += poi_poi_count
            co_occurrence_list_dict_attr[f"{poi2}+{poi1}"][0] += poi_poi_count

# Return the updated co-occurrence dictionary
co_occurrence_list_dict_attr


0
300
600
900
1200
1500
1800
2100
2400
2700
3000
3300
3600
3900
4200
4500
4800
5100
5400
5700
6000
6300


{'0+1': [181, 0],
 '0+2': [32, 0],
 '0+3': [61, 0],
 '0+4': [267, 0],
 '0+5': [11, 0],
 '0+6': [19, 0],
 '0+7': [164, 0],
 '0+8': [10, 0],
 '0+9': [7, 0],
 '0+10': [6, 0],
 '0+11': [170, 0],
 '0+12': [177, 0],
 '0+13': [120, 0],
 '0+14': [5, 0],
 '0+15': [172, 0],
 '0+16': [69, 0],
 '0+17': [10, 0],
 '0+18': [13, 0],
 '0+19': [13, 0],
 '0+20': [27, 0],
 '0+21': [59, 0],
 '0+22': [10, 0],
 '0+23': [9, 0],
 '0+24': [65, 0],
 '0+25': [26, 0],
 '0+26': [3, 0],
 '0+27': [15, 0],
 '0+28': [47, 0],
 '0+29': [33, 0],
 '0+30': [34, 0],
 '0+31': [8, 0],
 '0+32': [85, 0],
 '0+33': [136, 0],
 '0+34': [44, 0],
 '0+35': [253, 0],
 '0+36': [8, 0],
 '0+37': [0, 0],
 '0+38': [61, 0],
 '0+39': [176, 0],
 '0+40': [178, 0],
 '0+41': [39, 0],
 '0+42': [169, 0],
 '0+43': [1, 0],
 '0+44': [40, 0],
 '0+45': [43, 0],
 '0+46': [9, 0],
 '0+47': [7, 0],
 '0+48': [25, 0],
 '0+49': [33, 0],
 '0+50': [25, 0],
 '0+51': [9, 0],
 '0+52': [22, 0],
 '0+53': [9, 0],
 '0+54': [12, 0],
 '0+55': [14, 0],
 '0+56': [4, 0],
 '0

In [27]:
# Save only edges that have a co-occurrence relationship
co_occurrence_list_dict_attr2 = {
    k: v for k, v in co_occurrence_list_dict_attr.items() if v[0] != 0
}

# Extract POI coordinates (latitude and longitude)
poi_coords = poi_data[['latitude', 'longitude']].to_numpy()

for key in co_occurrence_list_dict_attr2.keys():
    u, v = map(int, key.split("+"))  # Convert the key into two POI indices

    # Compute the distance between the two POIs
    dis = distance(poi_coords[u][0], poi_coords[u][1], poi_coords[v][0], poi_coords[v][1])

    # Update the distance attribute for the co-occurrence edge
    co_occurrence_list_dict_attr2[key][1] = dis

# Return the updated dictionary
co_occurrence_list_dict_attr2


{'0+1': [181, 2.743010375853035],
 '0+2': [32, 2.6036817589918138],
 '0+3': [61, 2.2274793625382108],
 '0+4': [267, 2.0132036685738894],
 '0+5': [11, 2.107379500048001],
 '0+6': [19, 3.5173270697689696],
 '0+7': [164, 4.012326592697935],
 '0+8': [10, 5.567492691666253],
 '0+9': [7, 5.677902437599288],
 '0+10': [6, 5.7779201175300825],
 '0+11': [170, 4.158262672772868],
 '0+12': [177, 4.407105252571968],
 '0+13': [120, 2.9297195435961756],
 '0+14': [5, 5.991703299247377],
 '0+15': [172, 4.170842940628133],
 '0+16': [69, 2.9730902356147566],
 '0+17': [10, 4.368952202995491],
 '0+18': [13, 4.4714169838360105],
 '0+19': [13, 4.5288344854321085],
 '0+20': [27, 4.5585179190779135],
 '0+21': [59, 3.8061286246633754],
 '0+22': [10, 4.400915192765714],
 '0+23': [9, 4.537980672454361],
 '0+24': [65, 4.787459681505058],
 '0+25': [26, 2.8244790982619676],
 '0+26': [3, 5.8869089334879625],
 '0+27': [15, 3.2077285551480705],
 '0+28': [47, 2.9246950916877212],
 '0+29': [33, 17.238208363721373],
 '0+3

In [28]:
co_occurrence_list_index2=[]
co_occurrence_list_dict_attr3=[]
for x in co_occurrence_list_dict_attr2.keys():

    x2=x.split("+", 1)
    attr=co_occurrence_list_dict_attr2[x]
    co_occurrence_list_index2.append((int(x2[0]),int(x2[1])))
    co_occurrence_list_dict_attr3.append(attr)
# co_occurrence_list_index2

np.save("multigraph/"+city+"/co_occurrence_list_index.npy",torch.tensor(np.array(co_occurrence_list_index2)).t().contiguous())
np.save("multigraph/"+city+"/co_occurrence_attr.npy",co_occurrence_list_dict_attr3)